In [1]:
import numpy as np
import scipy.spatial.distance as dist
import matplotlib.pyplot as plt
import librosa as lb
import os.path
from pathlib import Path
import pickle
import multiprocessing
import time
import gc
from numba import jit, njit, float64, uint32, boolean

## DTW and Subsequence DTW

In [2]:
DTWDefaultSteps = np.array([[1, 1, 2],
                            [1, 2, 1]], dtype = np.uint32)

DTWDefaultWeights = np.array([2, 3, 3], dtype = np.float64)


subseqDTWDefaultSteps = np.array([[1, 1, 2],
                                  [1, 2, 1]], dtype = np.uint32)

subseqDTWDefaultWeights = np.array([1, 1, 2], dtype = np.float64)


MAX_FLOAT = float('inf')

In [3]:
featureFile1 = "implementation_test/test_features/Features_1.npy"
featureFile2 = "implementation_test/test_features/Features_2.npy"
featureFile3 = "implementation_test/test_features/Features_3.npy"
featureFile4 = "implementation_test/test_features/Features_4.npy"

In [4]:
# njit is equivalent to jit(nopython=True)
# This forces numba to compile in nopython mode, which is faster

@njit
def DTW_Cost_To_DandB(C, Steps = DTWDefaultSteps, weights = DTWDefaultWeights, subsequence=False):
    '''
    Find the accumulated cost matrix and backtrace matrix from a cost matrix using Dynamic time warping
    
    Arguments:
    C -- The Cost matrix
    Steps -- The available steps, where the first row is the row steps, the second row is the column steps
    weights -- The weights of the steps
    subsequence -- True if subsequence DTW should be performed rather than standard DTW
             
    Returns:
    D -- The accumulated cost matrix
    B -- The backtrace matrix
    '''
    '''
    Section for verifying input
    '''
    # Ensure parameters have correct dtypes and dimensions
#     try:
#         C = C.astype(np.float64)
#         assert C.ndim == 2
#     except:
#         print("FAILURE: The type of the cost matrix is wrong - please pass in a 2-d numpy array")
#         return
    
#     try:
#         Steps = Steps.astype(np.uint32)
#         assert Steps.ndim == 2
#     except:
#         print("FAILURE: The type of the steps matrix is wrong - please pass in a 2-d numpy array")
#         return
    
#     try:
#         weights = weights.astype(np.float64)
#         assert weights.ndim == 1
#     except:
#         print("FAILURE: The type of the steps matrix is wrong - please pass in a 2-d numpy array")
#         return
    
#     # Ensure steps and weights sizes are appropriate
#     stepsShape = Steps.shape
#     numDifSteps = len(weights)
    
#     if stepsShape[0] != 2:
#         print("FAILURE: The size of the steps matrix is wrong - please pass in a 2-d numpy array with 2 rows")
#         return
#     if stepsShape[1] != numDifSteps:
#         print("FAILURE: The number of steps and weights do not line up - please make sure that there are the same number of steps and weights")
#         return
    
    '''
    Algorithm
    '''
    # Separate steps
    rowSteps = Steps[0,:]
    colSteps = Steps[1,:]

    # Define Relevant Variables
    numRows = C.shape[0]
    numCols = C.shape[1]
    
    numDifSteps = len(weights)
    maxRowStep = max(rowSteps)
    maxColStep = max(colSteps)
    
    # Set up accumulated cost matrix D and backtrace matrix B
    D = np.ones((numRows + maxRowStep, numCols + maxColStep), dtype = np.float64) * MAX_FLOAT
    B = np.zeros((numRows, numCols), dtype = np.uint32)
    
    # Fill up D and B
    if subsequence:  # Initialize entire bottom row of D for subsequence
        D[maxRowStep, maxColStep:] = C[0,:]
    else:
        D[maxRowStep, maxColStep] = C[0,0]  # Initialize bottom corner if for standard DTW
    for row in range(maxRowStep, numRows + maxRowStep, 1):
        for col in range(maxColStep, numCols + maxColStep, 1):
            bestCost = D[row, col]
            bestCostIndex = 0
            # Go through each step, find the best one
            for stepIndex in range(numDifSteps):
                costForStep = D[row - rowSteps[stepIndex], col - colSteps[stepIndex]] + weights[stepIndex] * C[row - maxRowStep, col - maxColStep]
                if costForStep < bestCost:
                    bestCost = costForStep
                    bestCostIndex = stepIndex
            # Save best cost and step
            D[row,col] = bestCost
            B[row - maxRowStep, col - maxColStep] = bestCostIndex
    # Return accumulated cost matrix D and backtrace matrix B
    return D[maxRowStep:, maxColStep:], B

In [5]:
@njit
def DTW_Backtrace(D, B, Steps=DTWDefaultSteps, subsequence=False, startCol=-1):
    '''
    Backtrace through an accumulated cost matrix and backtrace matrix to find a path
    
    Arguments:
    D -- The accumulated cost matrix
    B -- The backtrace matrix
    Steps -- The available steps
    subsequence -- True if subsequence DTW should be performed rather than standard DTW
    startCol -- The column to begin backtracing from, or -1 if not specified
    
    Returns:
    fwdPath -- A 2d numpy array storing the optimal path. The first row is the path through the rows.
            The second row is the path through the columns
    '''
    '''
    Section for verifying input
    '''
    # Ensure parameters have correct dtypes and dimensions
#     try:
#         D = D.astype(np.float64)
#         assert D.ndim == 2
#     except:
#         print("FAILURE: The type of the accumulated cost matrix is wrong - please pass in a 2-d numpy array")
#         return

#     try:
#         B = B.astype(np.uint32)
#         assert B.ndim == 2
#     except:
#         print("FAILURE: The type of the backtrace matrix is wrong - please pass in a 2-d numpy array")
#         return
    
#     try:
#         Steps = Steps.astype(np.uint32)
#         assert Steps.ndim == 2
#     except:
#         print("FAILURE: The type of the steps matrix is wrong - please pass in a 2-d numpy array")
#         return

#     # Ensure that D and B are the same shape
#     if D.shape != B.shape:
#         print("FAILURE: The accumulated cost matrix and backtrace matrix are not the same size - please make sure their sizes match")
#         return
    
    
    '''
    Backtrace through D and B
    '''
    # Separate steps
    rowSteps = Steps[0,:]
    colSteps = Steps[1,:]
    
    # Initialize variables
    numRows = D.shape[0]
    numCols = D.shape[1]
    
    curRow = numRows - 1  # Always start at last row
    curCol = numCols - 1  # Standard DTW: Start at top-right corner
    if startCol >= 0:
        curCol = startCol
    elif subsequence:  # Subsequence: Choose lowest cost of top row
        curCol = np.argmin(D[numRows-1,:])
    
    endCol = curCol
    endCost = D[curRow, curCol]
    stepsInPath = 1
    stepIndex = 0
    done = (subsequence and curRow == 0) or (curRow == 0 and curCol == 0)
    path = np.zeros((2, numRows + numCols), dtype=np.uint32) # make as large as could need, then chop at the end
    path[0, 0] = curRow
    path[1, 0] = curCol
    
    # Backtrace
    while not done:
        
        if D[curRow, curCol] == MAX_FLOAT:  # No path exists to current location
            break
        
        # you're done if you've made it to the bottom left (non sub-sequence)
        # or just the bottom (sub-sequence)
        # find the step size
        curStepIndex = B[curRow, curCol]
        curRowStep = rowSteps[curStepIndex]
        curColStep = colSteps[curStepIndex]
        # backtrack by 1 step
        curRow = curRow - curRowStep
        curCol = curCol - curColStep
        # add your new location onto the path
        path[0, stepsInPath] = curRow
        path[1, stepsInPath] = curCol
        stepsInPath = stepsInPath + 1
        # check to see if you're done
        done = (subsequence and curRow == 0) or (curRow == 0 and curCol == 0)
        
    # reverse the path (a matrix with two rows) and return it
    fwdPath = np.fliplr(path[:, 0:stepsInPath])
    return fwdPath
    #return fwdPath, endCol, endCost

In [6]:
# Compile this function in object mode to allow for np.load and time profiling
@jit(forceobj = True)
def DTW(queryFeatureFile, refFeatureFile, Steps = DTWDefaultSteps, weights = DTWDefaultWeights, subsequence = False, \
        outfile = None, profile = False):
    '''
    Run DTW on query and reference feature matrices
    
    Arguments:
    queryFeatureFile -- The file containing the query feature matrix
    refFeatureFile -- The file containing the reference feature matrix
    Steps -- The steps matrix. The first row is the steps in along the rows,
             the second row is the steps along the columns
    weights -- The weights for the steps
    subsequence -- True if subsequence DTW should be performed rather than standard DTW
    
    Returns:
    path -- A 2d numpy array storing the optimal path. The first row is the path through the rows.
            The second row is the path through the columns
    '''
    # Extract Feature matrices
    F1 = np.load(queryFeatureFile, allow_pickle = True)
    F2 = np.load(refFeatureFile, allow_pickle = True)
    
    # empty file if no valid path possible
    if not subsequence and max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2:
        if outfile:
            pickle.dump(None, open(outfile, 'wb'))
        return None
    
    # start time logging
    times = []
    times.append(time.time())
    
    # Compute Cost Matrix
    C = 1 - F1.T @ F2 # cos distance metric
    
    times.append(time.time())
    
    # Get D and B
    D, B = DTW_Cost_To_DandB(C, Steps = Steps, weights = weights, subsequence=subsequence)
    
    times.append(time.time())
    
    # Backtrace and return
    wp = DTW_Backtrace(D, B, Steps=Steps, subsequence=subsequence)
    
    times.append(time.time())
    
    # logging result if outfile exists
    if outfile:
        pickle.dump(wp, open(outfile, 'wb'))
    
    # return extra timing array if profiling timing
    if profile:
        return wp, np.diff(times)
    else:
        return wp

In [7]:
def DTW_batch(querylist, featdir1, featdir2, outdir, n_cores, steps, weights, subsequence):
    
    outdir.mkdir(parents=True, exist_ok=True)
    
    # prep inputs for parallelization
    inputs = []
    with open(querylist, 'r') as f:
        for line in f:
            parts = line.strip().split(' ')
            assert len(parts) == 2
            featfile1 = (featdir1 / parts[0]).with_suffix('.npy')
            featfile2 = (featdir2 / parts[1]).with_suffix('.npy')
            queryid = os.path.basename(parts[0]) + '__' + os.path.basename(parts[1])
            outfile = (outdir / queryid).with_suffix('.pkl')
            if os.path.exists(outfile):
                print(f"Skipping {outfile}")
            else:
                inputs.append((featfile1, featfile2, steps, weights, subsequence, outfile))

    # process files in parallel
    pool = multiprocessing.Pool(processes = n_cores)
    pool.starmap(DTW, inputs)
    
    return

Performing Subsequence DTW alignments on training files

In [8]:
# query_list = 'cfg_files/query.train.list'
# featdir1 = Path('features/clean')
# featdir2 = Path('features/clean') # in case you want to align clean vs noisy
# outdir = Path('experiments_train/subsequence_dtw_clean')
# n_cores = 10
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([2,3,3])
# downsample = 1
# inputs = DTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, True)

Performing DTW alignments on training files

In [9]:
# query_list = 'cfg_files/query.train.list'
# featdir1 = Path('features/clean')
# featdir2 = Path('features/clean') # in case you want to align clean vs noisy
# outdir = Path('experiments_train/dtw_clean')
# n_cores = 10
# steps = DTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = DTWDefaultWeights #np.array([2,3,3])
# downsample = 1
# inputs = DTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, False)

Performing DTW alignments on test files

In [10]:
# query_list = 'cfg_files/query.test.list'
# featdir1 = Path('features/clean')
# featdir2 = Path('features/clean') # in case you want to align clean vs noisy
# outdir = Path('experiments_test/dtw_clean')
# n_cores = 10
# steps = DTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = DTWDefaultWeights #np.array([2,3,3])
# downsample = 1
# inputs = DTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, False)

### Test DTW on Random Feature Matrices

In [11]:
def genRandomFeatures(outdir):
    '''
    Generate random feature matrices and save them to outdir
    
    Arguments:
    outdir -- The directory to save the two feature matrices
    '''
    
    if not os.path.exists(outdir):
        os.mkdir(outdir)

    F1 = np.random.rand(12, 10000)
    norm_factor = np.sqrt(np.sum(F1*F1, axis=0))
    F1 = F1 / norm_factor

    F2 = np.random.rand(12, 10000)
    norm_factor = np.sqrt(np.sum(F2*F2, axis=0))
    F2 = F2 / norm_factor
    
    F3 = np.random.rand(12, 1000)
    norm_factor = np.sqrt(np.sum(F3*F3, axis=0))
    F3 = F3 / norm_factor

    F4 = np.random.rand(12, 1000)
    norm_factor = np.sqrt(np.sum(F4*F4, axis=0))
    F4 = F4 / norm_factor

    
    np.save(outdir / "Features_1.npy", F1)
    np.save(outdir / "Features_2.npy", F2)
    np.save(outdir / "Features_3.npy", F3)
    np.save(outdir / "Features_4.npy", F4)

In [12]:
# Make and save random features
#genRandomFeatures(Path("implementation_test/test_features"))
# Run this ^ once to create files for testing
# F1 = np.load("implementation_test/test_features/Features_1.npy", allow_pickle=True)
# F2 = np.load("implementation_test/test_features/Features_2.npy", allow_pickle=True)
# F3 = np.load("implementation_test/test_features/Features_3.npy", allow_pickle=True)
# F4 = np.load("implementation_test/test_features/Features_4.npy", allow_pickle=True)


In [13]:
#path = DTW(featureFile1, featureFile2)

In [14]:
#_, wp = lb.sequence.dtw(F1, F2, metric = 'cosine', step_sizes_sigma=DTWDefaultSteps.T, weights_mul = DTWDefaultWeights)

In [15]:
#np.allclose(path, np.fliplr(wp.T))

As desired, our implementation's output matches the output from librosa

### Test Subsequence DTW on Random Feature Matrices

In [16]:
#SDTWpath = DTW(featureFile3, featureFile1, Steps = subseqDTWDefaultSteps, weights=subseqDTWDefaultWeights, subsequence=True)

In [17]:
#_, SDTWwp = lb.sequence.dtw(F3, F1, metric = 'cosine', step_sizes_sigma=subseqDTWDefaultSteps.T, weights_mul = subseqDTWDefaultWeights, subseq=True)

In [18]:
#np.allclose(SDTWpath, np.fliplr(SDTWwp.T))

As desired, our implementation's output matches the output from librosa

## Non-ordered Segmental DTW

In [19]:
# Compile this function in object mode to allow for np.load and time profiling
@jit(forceobj = True)
def NSDTW(queryFeatureFile, refFeatureFile, segments, Steps = subseqDTWDefaultSteps, weights = subseqDTWDefaultWeights, \
          outfile = None, profile = False):
    '''
    Runs a non-ordered segmental DTW between query and reference features matrices
    
    Arguments:
    queryFeatureFile -- The file containing the query feature matrix
    refFeatureFile -- The file containing the reference feature matrix
    segments -- The number of segments to divide F1 into
    Steps -- The allowed steps
    weights -- The weights for the steps
    
    Returns:
    path -- The optimal non-ordered, segmented alignment path between F1 and F2
    '''
    # Extract Feature matrices
    F1 = np.load(queryFeatureFile, allow_pickle = True)
    F2 = np.load(refFeatureFile, allow_pickle = True)

    if max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2: # no valid path possible
        if outfile:
            pickle.dump(None, open(outfile, 'wb'))
        return None
    
    # start time logging
    times = []
    times.append(time.time())
    
    # Compute Cost
    # NOTE: This could also be done segment by segment.
    # I am doing it all up front to match the implementation in the old code.
    C = 1 - F1.T @ F2
    
    times.append(time.time())
    
    # Subsequence DTW each segment without backtracing
    segLength = int(np.ceil(F1.shape[1] / segments))
    Cseg = np.zeros((segments + 1, C.shape[1]), dtype = np.float64)
    Dparts = []
    Bparts = []
    for i in range(segments):
        segStart = i * segLength
        segEnd = min(segStart + segLength, C.shape[0])
        # Ensuring that the segment is contiguous here ensures best performance in later computations
        currentSeg = np.ascontiguousarray(C[segStart:segEnd,:])
        D_i, B_i = DTW_Cost_To_DandB(currentSeg, Steps = Steps, weights = weights, subsequence = True)
        
        # Store D_i and B_i for segment
        Dparts.append(D_i)
        Bparts.append(B_i)
    
    times.append(time.time())
    
    # Backtrace through segments with segment level path as guide
    # Initialize path: make as large as could need, then chop at the end
    path = []
    stepsInPath = 0
    # Frame level backtrace segment by segment
    for i in range(segments):
        pathSeg = DTW_Backtrace(Dparts[i], Bparts[i], Steps = Steps, subsequence = True)
        # Add offset to row indices so they match with overall path
        pathSeg[0,:] = pathSeg[0,:] + (i * segLength)

        # Append fragment to full path
        path.append(pathSeg.copy())
    
    wp_merged = np.hstack(path)
    
    times.append(time.time())
    
    if outfile:
        pickle.dump(wp_merged, open(outfile, 'wb'))

    if profile:
        return wp_merged, np.diff(times)
    else:
        return wp_merged

In [20]:
def SDTW_batch(querylist, featdir1, featdir2, outdir, n_cores, steps, weights, numSegments, fn):

    outdir.mkdir(parents=True, exist_ok=True)
    
    # prep inputs for parallelization
    inputs = []
    with open(querylist, 'r') as f:
        for line in f:
            parts = line.strip().split(' ')
            assert len(parts) == 2
            featfile1 = (featdir1 / parts[0]).with_suffix('.npy')
            featfile2 = (featdir2 / parts[1]).with_suffix('.npy')
            queryid = os.path.basename(parts[0]) + '__' + os.path.basename(parts[1])
            outfile = (outdir / queryid).with_suffix('.pkl')
            if os.path.exists(outfile):
                print(f"Skipping {outfile}")
            else:
                inputs.append((featfile1, featfile2, numSegments, steps, weights, outfile))

    # process files in parallel
    pool = multiprocessing.Pool(processes = n_cores)
    pool.starmap(fn, inputs)

    return

Performing NSDTW alignments on training files

In [21]:
# query_list = 'cfg_files/query.train.list'
# featdir1 = Path('features/clean')
# featdir2 = Path('features/clean') # in case you want to align clean vs noisy
# n_cores = 10
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# downsample = 1
# segmentVals = [2, 4, 8, 16, 32] 
# for numSegments in segmentVals:
#     outdir = Path(f'experiments_train/nsdtw_{numSegments}_clean')
#     try:
#         os.mkdir(outdir)
#     except:
#         print(outdir, " already exists")
#     SDTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, numSegments, NSDTW)

### Testing NSDTW on Random Feature Matrices

In [22]:
#NSDTWPath = NSDTW(featureFile1, featureFile2, 5)

In [23]:
#C = 1 - F1.T @ F2

In [24]:
#plt.imshow(C, origin="lower");
#plt.plot(NSDTWPath[1,:], NSDTWPath[0,:], 'r');

NOTE: I do not have anything to compare this to, but it seems visually correct

## Weakly-ordered Segmental DTW

In [25]:
@njit
def getSegmentEndingLocs(wp):
    '''
    Takes in a segment level path through and returns the columns where each segment ends
    
    Arguments:
    wp -- A segment level path (as a 2d numpy array with 2 rows)
    
    Returns:
    endLocs -- A list where the ith entry is the column where the ith segment ends
    '''
    prevLoc = wp[:,0] # [r,c]
    endLocs = []
    for i in range(wp.shape[1]):
        curLoc = wp[:,i]
        if curLoc[0] != prevLoc[0]: # if row changes
            endLocs.append(curLoc[1])
        prevLoc = curLoc
        
    return endLocs

In [26]:
# Compile this function in object mode to allow for np.load and time profiling
@jit(forceobj = True)
def WSDTW(queryFeatureFile, refFeatureFile, segments, Steps = subseqDTWDefaultSteps, weights = subseqDTWDefaultWeights, \
          outfile = None, profile = False):
    '''
    Runs a weakly-ordered segmental DTW between query and reference features matrices
    
    Arguments:
    queryFeatureFile -- The file containing the query feature matrix
    refFeatureFile -- The file containing the reference feature matrix
    segments -- The number of segments to divide F1 into
    Steps -- The allowed steps
    weights -- The weights for the steps
    
    Returns:
    path -- The optimal weakly-ordered, segmented alignment path between F1 and F2
    '''
    # Extract Feature matrices
    F1 = np.load(queryFeatureFile, allow_pickle = True)
    F2 = np.load(refFeatureFile, allow_pickle = True)

    if max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2: # no valid path possible
        if outfile:
            pickle.dump(None, open(outfile, 'wb'))
        return None
    
    # start time logging
    times = []
    times.append(time.time())
    
    # Compute Cost
    # NOTE: This could also be done segment by segment.
    # I am doing it all up front to match the implementation in the old code.
    C = 1 - F1.T @ F2
    
    times.append(time.time())
    
    # Subsequence DTW each segment without backtracing
    segLength = int(np.ceil(F1.shape[1] / segments))
    Cseg = np.zeros((segments + 1, C.shape[1]), dtype = np.float64)
    Dparts = []
    Bparts = []
    for i in range(segments):
        segStart = i * segLength
        segEnd = min(segStart + segLength, C.shape[0])
        # Ensuring that the segment is contiguous here ensures best performance in later computations
        currentSeg = np.ascontiguousarray(C[segStart:segEnd,:])
        D_i, B_i = DTW_Cost_To_DandB(currentSeg, Steps = Steps, weights = weights, subsequence = True)
        
        # Store D_i and B_i for segment and construct Cseg
        Dparts.append(D_i)
        Bparts.append(B_i)
        
        # NOTE: May need to separate this into a different loop for runtime profiling
        Cseg[i + 1,:] = D_i[-1,:]
    
    times.append(time.time())
    
    # run segment-level DTW (Not subsequence)
    segmentSteps = np.array([[0, 1],
                             [1, C.shape[0]//(2 * segments)]], #NOTE: This could cause differences with old implementation
                            dtype=np.uint32)
    segmentWeights = np.array([0, 1])
    
    Dseg, Bseg = DTW_Cost_To_DandB(Cseg, Steps = segmentSteps, weights = segmentWeights)
    
    times.append(time.time())
    
    wpseg = DTW_Backtrace(Dseg, Bseg, Steps=segmentSteps)
    
    times.append(time.time())
    
    # Backtrace through segments with segment level path as guide
    path = []
    # Frame level backtrace segment by segment
    segmentEndIdxs = getSegmentEndingLocs(wpseg)
        
    for i, endidx in enumerate(segmentEndIdxs):
        pathSeg = DTW_Backtrace(Dparts[i], Bparts[i], Steps = Steps, subsequence = True, startCol = endidx)
        # Add offset to row indices so they match with overall path
        pathSeg[0,:] = pathSeg[0,:] + (i * segLength)

        # Append fragment to full path
        path.append(pathSeg.copy())
    
    wp_merged = np.hstack(path)
    
    times.append(time.time())
    
    if outfile:
        pickle.dump(wp_merged, open(outfile, 'wb'))

    if profile:
        return wp_merged, np.diff(times)
    else:
        return wp_merged

Performing WSDTW alignments on training files

In [73]:
query_list = 'cfg_files/query.test.list'
featdir1 = Path('features/clean')
featdir2 = Path('features/clean') # in case you want to align clean vs noisy
n_cores = 10
steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
weights = subseqDTWDefaultWeights #np.array([1,1,2])
downsample = 1
segmentVals = [2, 4, 8, 16, 32] 
for numSegments in segmentVals:
    outdir = Path(f'experiments_train/test')
    try:
        os.mkdir(outdir)
    except:
        print(outdir, " already exists")
    SDTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, numSegments, WSDTW)

experiments_train/test  already exists


KeyboardInterrupt: 

Process ForkPoolWorker-162:
Traceback (most recent call last):
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
Process ForkPoolWorker-165:
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 121, in worker
    result = (True, func(*args, **kwds))
Traceback (most recent call last):
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 47, in starmapstar
    return list(itertools.starmap(args[0], args[1]))
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/site-packages/numpy/core/_asarray.py", line 141, in ascontiguousarray
    @set_module('numpy')
  File "/home/tshaw/anacon

### Testing WSDTW Results

In [28]:
#WSDTWPath = WSDTW(featureFile1, featureFile2, 5)

I will compare to results found using the cython implementation on the same random features matrices. Note that this will fail if the cython implementation hasn't been run the features

In [29]:
#cythonWSDTWPath = np.load("implementation_test/cython_results/WSDTW", allow_pickle = True)
#np.allclose(cythonWSDTWPath,WSDTWPath)

In [30]:
#WSDTWPath_10 = WSDTW(featureFile1, featureFile2, 10)
#cythonWSDTW_10 = np.load("implementation_test/cython_results/WSDTW_10seg", allow_pickle = True)
#np.allclose(cythonWSDTW_10, WSDTWPath_10)

In [31]:
#WSDTWPath_small = WSDTW(featureFile3, featureFile4, 5)
#cythonWSDTW_small = np.load("implementation_test/cython_results/WSDTW_small", allow_pickle = True)
#np.allclose(cythonWSDTW_small, WSDTWPath_small)

In [32]:
#plt.imshow(C, origin="lower");
#plt.plot(WSDTWPath[1,:], WSDTWPath[0,:], 'r');

The numba and cython implementations match :)

## Multithreded WSDTW

In [33]:
def WSDTW_multi(F1, F2, K, costMetric = "cos", profile = False):
    '''
    Runs a multi-threaded, parallelized weakly-ordered segmental DTW between two feature matrices
    
    Arguments:
    F1 -- The query feature matrix
    F2 -- The reference feature matrix
    K -- The number of segments to divide F1 into
    costMetric -- The cost metric to use to compute the cost matrix
    
    Returns:
    path -- The optimal weakly-ordered, segmented alignment path between F1 and F2
    '''
    if max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2: # no valid path possible
        if outfile:
            pickle.dump(None, open(outfile, 'wb'))
        return None
    
    # Set up variables
    frameSteps = np.array([[1, 1, 2],
                           [1, 2, 1]], dtype = np.uint32)

    frameWeights = np.array([1, 1, 2], dtype = np.float64)
    segLength = int(np.ceil(F1.shape[1] / K))
    
    times = []
    times.append(time.time())
    # DTW each segment in parallel
    # Set up task list
    tasks = [(F1, F2, costMetric, segLength, i) for i in range(K)]
    
    # Set up pool
    with multiprocessing.Pool(processes = K) as p:
        times.append(time.time())
         # Perform subsequence DTW on each segment in parallel
        segmentResults = p.starmap(DTWSegment, tasks)
        
    times.append(time.time())

    # Run segment-level DTW (Not subsequence)
    segmentSteps = np.array([[0, 1],
                             [1, F1.shape[1]//(2 * K)]],
                            dtype=np.uint32)
    segmentWeights = np.array([0, 1])
    
    Cseg = np.zeros((K + 1, F2.shape[1]), dtype = np.float64)
    for i, (D_i, _) in enumerate(segmentResults):
        Cseg[i+1,:] = D_i[-1,:]

    times.append(time.time())

    Dseg, Bseg = DTW_Cost_To_DandB(Cseg, Steps = segmentSteps, weights = segmentWeights)
    
    times.append(time.time())
    
    wpseg = DTW_Backtrace(Dseg, Bseg, Steps=segmentSteps)
    
    times.append(time.time())

    # Backtrace through segments with segment level path as guide
    # Set up task list (use segmentResults)
    segmentEndIdxs = getSegmentEndingLocs(wpseg)
    backtraceTasks = [(D, B, segmentEndIdxs[i], segLength, i) for i, (D, B) in enumerate(segmentResults)]
    
    # Perform backtrace in parallel
    with multiprocessing.Pool(processes = K) as p:
        pathSegments = p.starmap(backtraceSegment, backtraceTasks)
    times.append(time.time())
    
    # Compile path and return
    wp_merged = np.concatenate(pathSegments, axis = 1)
    if profile:
        return wp_merged, np.diff(times)
    else:
        return wp_merged

In [34]:
@jit(forceobj = True)
def DTWSegment(F1, F2, costMetric, segLength, segNum):
    '''
    Extracts a single segment of F1 and performs subsequence DTW between it and F2
    
    Arguments:
    F1 -- The query feature matrix
    F2 -- The reference feature matrix
    costMetric -- The cost metric to use to compute the cost matrix
    segLength -- The length of each segment of the query feature matrix
    segNum -- The index of the segment to use (0 to K-1, inclusive)
    
    Returns:
    D_i -- The accumulated cost matrix for the relevant segment
    B_i -- The backtrace matrix for the relevant segment
    '''
    # Get segment
    seg = extractSegment(F1, segLength, segNum)
    
    
    # Compute costs:
    C = dist.cdist(seg.T, F2.T, metric = costMetric)  # scipy's cdist wants dimensions reversed
    
    # DTW
    Steps = np.array([[1, 1, 2],
                      [1, 2, 1]], dtype = np.uint32)

    weights = np.array([1, 1, 2], dtype = np.float64)
    
    return DTW_Cost_To_DandB(C, Steps = Steps, weights = weights, subsequence = True)

In [35]:
@njit
def extractSegment(F1, segLength, segNum):
    '''
    Extracts a single segment of F1
    
    Arguments:
    F1 -- The query feature matrix
    segLength -- The length of each segment of the query feature matrix
    segNum -- The index of the segment to use (0 to K-1, inclusive)
    
    Returns:
    segment -- A single segment of F1
    '''
    segStart = segNum * segLength
    segEnd = min(segStart + segLength, F1.shape[1])
    # Ensuring that the segment is contiguous here ensures best performance in later computations
    return np.ascontiguousarray(F1[:,segStart:segEnd])

In [36]:
@njit
def backtraceSegment(D, B, startCol, segLength, segNum):
    '''
    Backtrace through a segment and return the path with the row indices offset so they match the overall path
    
    Arguments:
    D -- The cumulative cost matrix for the segment
    B -- The backtrace matrix for the segment
    startCol -- The column to start backtracing from
    segLength -- The length of each segment of the query feature matrix
    segNum -- The index of the segment to use (0 to K-1, inclusive)
    
    Returns:
    path -- The path through the segment with the row indices offset so they match the overall path
    '''
    # Set up variables
    Steps = np.array([[1, 1, 2],
                      [1, 2, 1]], dtype = np.uint32)
    
    # Backtrace
    path = DTW_Backtrace(D, B, Steps = Steps, subsequence = True, startCol = startCol)
    
    # Add offset to row indices so they match with overall path
    path[0,:] = path[0,:] + (segNum * segLength)
    return path

### Testing Multithreaded WSDTW

In [37]:
#path_multi = WSDTW_multi(F1, F2, 5, "cos")
#np.allclose(path_multi, WSDTWPath)

In [38]:
#path_multi_10 = WSDTW_multi(F1, F2, 10, "cos")
#np.allclose(path_multi_10, WSDTWPath_10)

In [39]:
#path_multi_small = WSDTW_multi(F3, F4, 5, "cos")
#np.allclose(path_multi_small, WSDTWPath_small)

## Further Parallelized WSDTW

In [40]:
def moreParallelWSDTW(F1, F2, K, M):
    '''
    Runs a more parallelized version of WSDTW
    
    Arguments:
    F1 -- The query feature matrix
    F2 -- The reference feature matrix
    K -- The number of fragments
    M -- The number of sub-fragments
    
    Returns:
    wp_merged -- The WSDTW path
    '''
    Steps = np.array([[1, 1, 2],
                      [1, 2, 1]], dtype = np.uint32)

    weights = np.array([1, 1, 2], dtype = np.float64)
    
    if max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2: # no valid path possible
        if outfile:
            pickle.dump(None, open(outfile, 'wb'))
        return None
    
    # Compute Cost
    # NOTE: This could also be done segment by segment.
    # I am doing it all up front to match the implementation in the old code.
    C = 1 - F1.T @ F2
    
    # Subsequence DTW each segment without backtracing
    segLength = int(np.ceil(F1.shape[1] / K))
    Cseg = np.zeros((K + 1, C.shape[1]), dtype = np.float64)
    Dparts = []
    Bparts = []
    for i in range(K):
        segStart = i * segLength
        segEnd = min(segStart + segLength, C.shape[0])
        # Ensuring that the segment is contiguous here ensures best performance in later computations
        currentSeg = np.ascontiguousarray(C[segStart:segEnd,:])
        # Further divide each segment into fragments
        D_i = np.zeros(currentSeg.shape)
        B_i = np.ones(currentSeg.shape)
        fragLength = int(np.ceil(currentSeg.shape[1] / M) + 2 * currentSeg.shape[0])
        for j in range(M):
            fragStart = j * fragLength - j * 2 * currentSeg.shape[0]
            fragEnd = min(fragStart + fragLength, currentSeg.shape[1])
            currentFrag = currentSeg[:, fragStart:fragEnd]
            
            D_frag, B_frag = DTW_Cost_To_DandB(currentFrag, Steps = Steps, weights = weights, subsequence = True)
            
            if fragStart == 0: # Use all of first fragment
                D_i[:, 0:fragEnd] = D_frag
                B_i[:, 0:fragEnd] = B_frag
            else: # Discard overlap for later fragments
                D_i[:, fragStart + 2 * currentSeg.shape[0]:fragEnd] = D_frag[:, 2 * currentSeg.shape[0]:]
                B_i[:, fragStart + 2 * currentSeg.shape[0]:fragEnd] = B_frag[:, 2 * currentSeg.shape[0]:]        
        # Store D_i and B_i for segment and construct Cseg
        Dparts.append(D_i)
        Bparts.append(B_i)
        
        # NOTE: May need to separate this into a different loop for runtime profiling
        Cseg[i + 1,:] = D_i[-1,:]

    # run segment-level DTW (Not subsequence)
    segmentSteps = np.array([[0, 1],
                             [1, C.shape[0]//(2 * K)]], #NOTE: This could cause differences with old implementation
                            dtype=np.uint32)
    segmentWeights = np.array([0, 1])
    
    Dseg, Bseg = DTW_Cost_To_DandB(Cseg, Steps = segmentSteps, weights = segmentWeights)
    wpseg = DTW_Backtrace(Dseg, Bseg, Steps=segmentSteps)
    
    # Backtrace through segments with segment level path as guide
    path = []
    # Frame level backtrace segment by segment
    segmentEndIdxs = getSegmentEndingLocs(wpseg)
    for i, endidx in enumerate(segmentEndIdxs):
        pathSeg = DTW_Backtrace(Dparts[i], Bparts[i], Steps = Steps, subsequence = True, startCol = endidx)
        # Add offset to row indices so they match with overall path
        pathSeg[0,:] = pathSeg[0,:] + (i * segLength)

        # Append fragment to full path
        path.append(pathSeg.copy())
    
    wp_merged = np.hstack(path)

    return wp_merged

### Testing Further parallelized WSDTW

In [41]:
#path_frag = moreParallelWSDTW(F1, F2, 5, 5)
#np.allclose(path_frag, WSDTWPath)

In [42]:
#path_frag = moreParallelWSDTW(F1, F2, 5, 10)
#np.allclose(path_frag, WSDTWPath)

In [43]:
#path_frag_10 = moreParallelWSDTW(F1, F2, 10, 50)
#np.allclose(path_frag_10, WSDTWPath_10)

## Strongly-ordered Segmental DTW

In [44]:
@njit
def SSDTW_Segment_Level_DTW(Cseg, Tseg):
    '''
    Performs the segment level DTW for strongly-ordered segmental DTW
    Steps not required because they are variable based on Tseg
    
    Arguments:
    Cseg -- The segment level cost matrix
    Tseg -- A matrix where the i,jth entry is the column of the optimal path through segment i ending at column j.
            This is used to determine the possible segment level steps that ensure strong ordering
            
    Returns:
    Dseg -- The segment level accumulated cost matrix
    Bseg -- The segment level backtrace matrix. Since steps are variable, the i, jth entry of the backtrace matrix
            stores either -1 for a (1, 0) "skip" step or the colStep value of a (1, colStep) step ending at i,j
    '''

    # Define Relevant Variables
    numRows = Cseg.shape[0]
    numCols = Cseg.shape[1]
    
    # Set up accumulated cost matrix D and backtrace matrix B
    Dseg = np.ones((numRows + 1, numCols), dtype = np.float64) * MAX_FLOAT
    Dseg[0,:] = 0
    
    # (0,1) transition by default
    Bseg = np.zeros((numRows+1, numCols), dtype = np.int32) - 1
    
    # Fill up D and B
    for row in range(1, numRows+1):
        for col in range(numCols):
            # (0,1) transition is skip with weight 0
            if col==0:
                skipCost = MAX_FLOAT
            else:
                skipCost = Dseg[row, col-1]
            Dseg[row, col] = skipCost
            
            traverseStartCol = Tseg[row-1,col]
            if traverseStartCol >= 0: # is it possible to traverse previous segment and end up here?
                # Traverse segment with weight 1
                traverseSegCost = Dseg[row-1, traverseStartCol] + Cseg[row-1, col]
                # If traversing here is best option, store the column where the path starts
                if traverseSegCost < skipCost:
                    Dseg[row, col] = traverseSegCost
                    # TraverseStartCol represents where to start backtracing in the next row
                    Bseg[row, col] = traverseStartCol
    
    return Dseg, Bseg

In [45]:
@njit
def SSDTW_Segment_Level_Backtrace(Dseg, Bseg):
    '''
    Backtraces through segments enforcing a strongly-ordered path
    
    Arguments:
    Dseg -- The segmental accumulated cost matrix
    Bseg -- The segmental backtrace matrix. Stores -1 for (0,1) transitions and colStep for (1, colStep) transitions
    
    Returns:
    path -- A vector where the ith element is the column where the ith segment should end
    '''
    # Initialize variables
    numRows = Dseg.shape[0]
    numCols = Dseg.shape[1]
    curRow = numRows - 1
    curCol = numCols - 1
    # Path will have one entry for every row except for the bottom one
    path = np.zeros(numRows-1, dtype = np.uint32)
    stepsInPath = 0
        
    # Backtrace until reaching bottom row
    while curRow > 0:
        
        if Dseg[curRow, curCol] == MAX_FLOAT:
            print('A path is not possible')
            break
        
        # (1,0) "skip" transitions (-1 in Bseg) do not get added to path
        if Bseg[curRow, curCol] < 0:
            curCol = curCol - 1
        # For segment traversals, store segment end location in the path.
        else:
            path[stepsInPath] = curCol
            # Continue backtracing where the segment tranversal began
            curCol = Bseg[curRow, curCol]
            curRow = curRow - 1
            stepsInPath = stepsInPath + 1
    # Remember to flip the backtraced path
    return path[::-1]

In [46]:
@njit
def calcTseg(D_i, B_i, Steps = subseqDTWDefaultSteps):
    '''
    Calculate a row of Tseg for SSDTW from the the accumulated cost and backtrace matrix for that segment
    
    Arguments:
    D_i -- The accumulated cost matrix for the ith segment
    B_i -- The backtrace matrix for the ith segment
    Steps -- The available steps
    
    Returns:
    Tseg_i -- The ith row of Tseg
    '''
    # Initializing variables
    numRows = D_i.shape[0]
    numCols = D_i.shape[1]
    rowSteps = Steps[0,:]
    colSteps = Steps[1,:]
    # Default to -1, meaning no path ending at that location is possible
    Tseg_i = np.zeros(numCols, dtype = np.uint32) - 1
    
    # Fill in Tseg_i by backtracing from each column
    # backtrace from every location
    for endCol in range(numCols):
        curCol = endCol
        curRow = numRows - 1
        while curRow > 0:
            if D_i[curRow, curCol] == MAX_FLOAT: # no valid path
                Tseg_i[curCol] = -1
                break

            curStepIndex = B_i[curRow, curCol]
            curRow = curRow - rowSteps[curStepIndex]
            curCol = curCol - colSteps[curStepIndex]
            if curRow == 0:
                Tseg_i[endCol] = curCol
    
    return Tseg_i

In [47]:
# Compile this function in object mode to allow for np.load and time profiling
@jit(forceobj = True)
def SSDTW(queryFeatureFile, refFeatureFile, segments, Steps = subseqDTWDefaultSteps, weights = subseqDTWDefaultWeights, \
          outfile=None, profile=False):
    '''
    Aligns query and reference with strictly-ordered segmental DTW
    
    Arguments:
    queryFeatureFile -- The file containing the query feature matrix
    refFeatureFile -- The file containing the reference feature matrix
    segments -- The number of segments
    Steps -- The allowable steps
    weights -- The weights of the steps
    
    Returns:
    path -- The optimal strictly ordered segmental path
    '''
    #print(queryFeatureFile, refFeatureFile)
    # Extract Feature matrices
    F1 = np.load(queryFeatureFile, allow_pickle = True)
    F2 = np.load(refFeatureFile, allow_pickle = True)
    
    # NOTE: This swap comes from the old code.
    # It is not mentioned in the paper but seems important because of the strictly increasing nature of the path
    # The swap is undone at the end of the function
    swap = (F1.shape[1] > F2.shape[1])
    if swap:
        F1, F2 = F2, F1 # make the shorter sequence the query
        
    
    if F2.shape[1] / F1.shape[1] >= 2: # no valid path possible
        if max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2: # no valid path possible
            if outfile:
                pickle.dump(None, open(outfile, 'wb'))
            return None
    
    # start time logging
    times = []
    times.append(time.time())
    
    # Compute Cost
    C = 1 - F1.T @ F2
    
    times.append(time.time())
        
    # Subsequence DTW each segment without backtracing
    segLength = int(np.ceil(F1.shape[1] / segments))
    Cseg = np.zeros((segments, C.shape[1]), dtype = np.float64)
    Tseg = np.zeros((segments, F2.shape[1]), dtype=np.int32)
    Dparts = []
    Bparts = []
    
    for i in range(segments):
        
        segStart = i * segLength
        segEnd = min(segStart + segLength, C.shape[0])
        # Ensuring that the segment is contiguous here ensures best performance in later computations
        currentSeg = np.ascontiguousarray(C[segStart:segEnd,:])
        D_i, B_i = DTW_Cost_To_DandB(currentSeg, Steps = Steps, weights = weights, subsequence = True)
        
        # Store D_i and B_i for segment and construct Cseg
        Dparts.append(D_i)
        Bparts.append(B_i)
        
    
    times.append(time.time())
    
    for i in range(segments):
        D_i = Dparts[i]
        B_i = Bparts[i]
        Cseg[i,:] = D_i[-1,:]
        Tseg[i,:] = calcTseg(D_i, B_i, Steps=Steps)
    
    times.append(time.time())
    # run segment-level DTW (Not subsequence)
    Dseg, Bseg = SSDTW_Segment_Level_DTW(Cseg, Tseg)
    
    times.append(time.time())
        
    segmentEndIdxs = SSDTW_Segment_Level_Backtrace(Dseg, Bseg)
    
    times.append(time.time())
    
    # Frame level backtrace segment by segment
    path = []
    for i, endidx in enumerate(segmentEndIdxs):
        pathSeg = DTW_Backtrace(Dparts[i], Bparts[i], Steps = Steps, subsequence = True, startCol = endidx)
        
        # Add offset to row indices so they match with overall path
        pathSeg[0,:] = pathSeg[0,:] + (i * segLength)

        # Append fragment to full path
        path.append(pathSeg.copy())
    
    wp_merged = np.hstack(path)
    
    times.append(time.time())
    
    # Again, this swap is based on the old implementation
    if swap:
        wp_merged = np.flipud(wp_merged) # undo swap
        
    if outfile:
        pickle.dump(wp_merged, open(outfile, 'wb'))
    
    if profile:
        return wp_merged, np.diff(times)
    else:
        return wp_merged

Performing SSDTW alignments on training files

In [48]:
# q_list = 'cfg_files/query.train.list'
# exp_dir = 'experiments_train/'

# mismatch_files = []
# flipped = []
# numba_nonexist_files = []
# cython_nonexist_files = []
# segment_values = [2, 4, 8, 16, 32]
# for num_segs in segment_values:
#     print(num_segs)
#     count = 0
#     with open(q_list, 'r') as f:
#         for line in f:
#             parts = line.strip().split(' ')
#             assert len(parts) == 2
#             queryid = os.path.basename(parts[0]) + '__' + os.path.basename(parts[1])
#             outfile = Path(queryid).with_suffix('.pkl')
            
#             numba_dir = Path(exp_dir + 'ssdtw_' + str(num_segs) + '_clean') / outfile
#             cython_dir = Path(exp_dir + 'ssdtw_cython_' + str(num_segs) + '_clean') / outfile
            
#             if not os.path.exists(numba_dir):
#                 numba_nonexist_files.append(outfile)
#                 continue
            
#             if not os.path.exists(cython_dir):
#                 cython_nonexist_files.append(outfile)
#                 continue
            
#             if np.load(numba_dir, allow_pickle=True) is not None:
#                 if not np.allclose(np.load(numba_dir, allow_pickle=True), np.load(cython_dir, allow_pickle=True)):
#                     mismatch_files.append(outfile)
#                     count += 1

#                     if np.allclose(np.flipud(np.load(numba_dir, allow_pickle=True)),np.load(cython_dir, allow_pickle=True)):
#                         flipped.append(outfile)
    
#                 print(outfile)
#                 print(np.sum(np.equal(np.flipud(np.load(numba_dir, allow_pickle=True)), np.load(cython_dir, allow_pickle=True))))
#                 print(np.load(numba_dir, allow_pickle=True).shape[0] * np.load(numba_dir, allow_pickle=True).shape[1])
#                 print(np.load(numba_dir, allow_pickle=True)[:,:10])
#                 print(np.load(cython_dir, allow_pickle=True)[:,:10])


In [49]:
# len(mismatch_files)

In [50]:
# len(flipped)

In [51]:
# len(numba_nonexist_files)

In [52]:
# len(cython_nonexist_files)

In [72]:
# query_list = 'cfg_files/query.train.list'
# featdir1 = Path('features/clean')
# featdir2 = Path('features/clean') # in case you want to align clean vs noisy
# n_cores = 10
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# downsample = 1
# segmentVals = [2, 4, 8, 16, 32] 
# for numSegments in segmentVals:
#     print(numSegments)
#     outdir = Path(f'experiments_train/ssdtw_{numSegments}_clean')
#     try:
#         os.mkdir(outdir)
#     except:
#         print(outdir, " already exists")
#     SDTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, numSegments, SSDTW)

2


TypeError: not enough arguments: expected 7, got 6

Process ForkPoolWorker-155:
Process ForkPoolWorker-159:
Process ForkPoolWorker-153:
Process ForkPoolWorker-152:
Process ForkPoolWorker-156:
Process ForkPoolWorker-157:
Process ForkPoolWorker-158:
Process ForkPoolWorker-154:
Process ForkPoolWorker-151:
Process ForkPoolWorker-160:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocess

In [54]:
# cythonSSDTWPath_small = np.load("implementation_test/cython_results/SSDTW_small", allow_pickle = True)
# SSDTWPath_small = SSDTW(featureFile3, featureFile4, 5)
# np.allclose(cythonSSDTWPath_small, SSDTWPath_small)

In [55]:
#C2 = 1 - F3.T @ F4

In [56]:
#plt.imshow(C2, origin="lower");
#plt.plot(cythonSSDTWPath_small[1,:], cythonSSDTWPath_small[0,:], 'r');

In [57]:
# cythonSSDTWPath = np.load("implementation_test/cython_results/SSDTW", allow_pickle = True)
# SSDTWPath = SSDTW(featureFile1, featureFile2, 5)
# np.allclose(cythonSSDTWPath, SSDTWPath)

In [58]:
%matplotlib inline
%load_ext Cython

In [59]:
%%cython
import numpy as np
cimport numpy as np
cimport cython

import sys
import time


DTYPE_INT32 = np.int32
ctypedef np.int32_t DTYPE_INT32_t

DTYPE_FLOAT = np.float64
ctypedef np.float64_t DTYPE_FLOAT_t

cdef DTYPE_FLOAT_t MAX_FLOAT = float('inf')

# careful, without bounds checking can mess up memory - also can't use negative indices I think (like x[-1])
@cython.boundscheck(False) # turn off bounds-checking for entire function
def DTW_Cost_To_AccumCostAndSteps(Cin, parameter):
    '''
    Inputs
        C: The cost Matrix
    '''


    '''
    Section for checking and catching errors in the inputs
    '''
    
    cdef np.ndarray[DTYPE_FLOAT_t, ndim=2] C
    try:
        C = np.array(Cin, dtype=DTYPE_FLOAT)
    except TypeError:
        print(bcolors.FAIL + "FAILURE: The type of the cost matrix is wrong - please pass in a 2-d numpy array" + bcolors.ENDC)
        return [-1, -1, -1]
    except ValueError:
        print(bcolors.FAIL + "FAILURE: The type of the elements in the cost matrix is wrong - please have each element be a float (perhaps you passed in a matrix of ints?)" + bcolors.ENDC)
        return [-1, -1, -1]
    
    cdef np.ndarray[np.uint32_t, ndim=1] dn
    cdef np.ndarray[np.uint32_t, ndim=1] dm
    cdef np.ndarray[DTYPE_FLOAT_t, ndim=1] dw
    # make sure dn, dm, and dw are setup
    # dn loading and exception handling
    if ('dn'  in parameter.keys()):
        try:

            dn = np.array(parameter['dn'], dtype=np.uint32)
        except TypeError:
            print(bcolors.FAIL + "FAILURE: The type of dn (row steps) is wrong - please pass in a 1-d numpy array that holds uint32s" + bcolors.ENDC)
            return [-1, -1, -1]
        except ValueError:
            print(bcolors.FAIL + "The type of the elements in dn (row steps) is wrong - please have each element be a uint32 (perhaps you passed a long?). You can specify this when making a numpy array like: np.array([1,2,3],dtype=np.uint32)" + bcolors.ENDC)
            return [-1, -1, -1]
    else:
        dn = np.array([1, 1, 0], dtype=np.uint32)
    # dm loading and exception handling
    if 'dm'  in parameter.keys():
        try:
            dm = np.array(parameter['dm'], dtype=np.uint32)
        except TypeError:
            print(bcolors.FAIL + "FAILURE: The type of dm (col steps) is wrong - please pass in a 1-d numpy array that holds uint32s" + bcolors.ENDC)
            return [-1, -1, -1]
        except ValueError:
            print(bcolors.FAIL + "FAILURE: The type of the elements in dm (col steps) is wrong - please have each element be a uint32 (perhaps you passed a long?). You can specify this when making a numpy array like: np.array([1,2,3],dtype=np.uint32)" + bcolors.ENDC)
            return [-1, -1, -1]
    else:
        print(bcolors.FAIL + "dm (col steps) was not passed in (gave default value [1,0,1]) " + bcolors.ENDC)
        dm = np.array([1, 0, 1], dtype=np.uint32)
    # dw loading and exception handling
    if 'dw'  in parameter.keys():
        try:
            dw = np.array(parameter['dw'], dtype=DTYPE_FLOAT)
        except TypeError:
            print(bcolors.FAIL + "FAILURE: The type of dw (step weights) is wrong - please pass in a 1-d numpy array that holds floats" + bcolors.ENDC)
            return [-1, -1, -1]
        except ValueError:
            print(bcolors.FAIL + "FAILURE:The type of the elements in dw (step weights) is wrong - please have each element be a float (perhaps you passed ints or a long?). You can specify this when making a numpy array like: np.array([1,2,3],dtype=np.float64)" + bcolors.ENDC)
            return [-1, -1, -1]
    else:
        dw = np.array([1, 1, 1], dtype=DTYPE_FLOAT)
        print(bcolors.FAIL + "dw (step weights) was not passed in (gave default value [1,1,1]) " + bcolors.ENDC)
    
    
    '''
    Section where types are given to the variables we're going to use 
    '''
    # create matrices to store our results (D and E)
    cdef DTYPE_INT32_t numRows = C.shape[0] # only works with np arrays, use np.shape(x) will work on lists? want to force to use np though?
    cdef DTYPE_INT32_t numCols = C.shape[1]
    cdef DTYPE_INT32_t numDifSteps = np.size(dw)

    cdef unsigned int maxRowStep = max(dn)
    cdef unsigned int maxColStep = max(dm)

    cdef np.ndarray[np.uint32_t, ndim=2] steps = np.zeros((numRows,numCols), dtype=np.uint32)
    cdef np.ndarray[DTYPE_FLOAT_t, ndim=2] accumCost = np.ones((maxRowStep + numRows, maxColStep + numCols), dtype=DTYPE_FLOAT) * MAX_FLOAT

    cdef DTYPE_FLOAT_t bestCost
    cdef DTYPE_INT32_t bestCostIndex
    cdef DTYPE_FLOAT_t costForStep
    cdef unsigned int row, col
    cdef unsigned int stepIndex

    '''
    The start of the actual algorithm, now that all our variables are set up
    '''
    # initializing the cost matrix - depends on whether its subsequence DTW
    # essentially allow us to hop on the bottom anywhere (so could start partway through one of the signals)
    if parameter['SubSequence']:
        for col in range(numCols):
            accumCost[maxRowStep, col + maxColStep] = C[0, col]
    else:
        accumCost[maxRowStep, maxColStep] = C[0,0]
    
    # filling the accumulated cost matrix
    for row in range(maxRowStep, numRows + maxRowStep, 1):
        for col in range(maxColStep, numCols + maxColStep, 1):
            bestCost = accumCost[<unsigned int>row, <unsigned int>col] # initialize with what's there - so if is an entry point, then can start low
            bestCostIndex = 0
            # go through each step, find the best one
            for stepIndex in range(numDifSteps):
                #costForStep = accumCost[<unsigned int>(row - dn[<unsigned int>(stepIndex)]), <unsigned int>(col - dm[<unsigned int>(stepIndex)])] + dw[<unsigned int>(stepIndex)] * C[<unsigned int>(row - maxRowStep), <unsigned int>(col - maxColStep)]
                costForStep = accumCost[<unsigned int>((row - dn[(stepIndex)])), <unsigned int>((col - dm[(stepIndex)]))] + dw[<unsigned int>(stepIndex)] * C[<unsigned int>(row - maxRowStep), <unsigned int>(col - maxColStep)]
                if costForStep < bestCost:
                    bestCost = costForStep
                    bestCostIndex = stepIndex
            # save the best cost and best cost index
            accumCost[row, col] = bestCost
            steps[<unsigned int>(row - maxRowStep), <unsigned int>(col - maxColStep)] = bestCostIndex
    # return the accumulated cost along with the matrix of steps taken to achieve that cost
    return [accumCost[maxRowStep:, maxColStep:], steps]

@cython.boundscheck(False) # turn off bounds-checking for entire function
def DTW_GetPath(np.ndarray[DTYPE_FLOAT_t, ndim=2] accumCost, np.ndarray[np.uint32_t, ndim=2] stepsForCost, parameter):
    '''

    Parameter should have: 'dn', 'dm', 'dw', 'SubSequence'
    '''

    cdef np.ndarray[unsigned int, ndim=1] dn
    cdef np.ndarray[unsigned int, ndim=1] dm
    cdef np.uint8_t subseq
    cdef np.int32_t startCol # added
    # make sure dn, dm, and dw are setup
    if ('dn'  in parameter.keys()):
        dn = parameter['dn']
    else:
        dn = np.array([1, 1, 0], dtype=DTYPE_INT32)
    if 'dm'  in parameter.keys():
        dm = parameter['dm']
    else:
        dm = np.array([1, 0, 1], dtype=DTYPE_INT32)
    if 'SubSequence' in parameter.keys():
        subseq = parameter['SubSequence']
    else:
        subseq = 0
    
    # added START
    if 'startCol' in parameter.keys(): 
        startCol = parameter['startCol']
    else:
        startCol = -1
    # added END

    cdef np.uint32_t numRows
    cdef np.uint32_t numCols
    cdef np.uint32_t curRow
    cdef np.uint32_t curCol
    cdef np.uint32_t endCol
    cdef DTYPE_FLOAT_t endCost

    numRows = accumCost.shape[0]
    numCols = accumCost.shape[1]

    # either start at the far corner (non sub-sequence)
    # or start at the lowest cost entry in the last row (sub-sequence)
    # where all of the signal along the row has been used, but only a 
    # sub-sequence of the signal along the columns has to be used
    curRow = numRows - 1
    if subseq:
        curCol = np.argmin(accumCost[numRows - 1, :])
    else:
        curCol = numCols - 1
        
    # added - if specified, overrides above
    if startCol >= 0:
        curCol = startCol

    endCol = curCol
    endCost = accumCost[curRow, curCol]

    cdef np.uint32_t curRowStep
    cdef np.uint32_t curColStep
    cdef np.uint32_t curStepIndex


    cdef np.ndarray[np.uint32_t, ndim=2] path = np.zeros((2, numRows + numCols), dtype=np.uint32) # make as large as could need, then chop at the end
    path[0, 0] = curRow
    path[1, 0] = curCol

    cdef np.uint32_t stepsInPath = 1 # starts at one, we add in one before looping
    cdef np.uint32_t stepIndex = 0
    cdef np.int8_t done = (subseq and curRow == 0) or (curRow == 0 and curCol == 0)
    while not done:
        if accumCost[curRow, curCol] == MAX_FLOAT:
            print('A path is not possible')
            break

        # you're done if you've made it to the bottom left (non sub-sequence)
        # or just the bottom (sub-sequence)
        # find the step size
        curStepIndex = stepsForCost[curRow, curCol]
        curRowStep = dn[curStepIndex]
        curColStep = dm[curStepIndex]
        # backtrack by 1 step
        curRow = curRow - curRowStep
        curCol = curCol - curColStep
        # add your new location onto the path
        path[0, stepsInPath] = curRow
        path[1, stepsInPath] = curCol
        stepsInPath = stepsInPath + 1
        # check to see if you're done
        done = (subseq and curRow == 0) or (curRow == 0 and curCol == 0)

    # reverse the path (a matrix with two rows) and return it
    return [np.fliplr(path[:, 0:stepsInPath]), endCol, endCost]

class bcolors:
    HEADER = '\033[95m'
    OKBLUE = '\033[94m'
    OKGREEN = '\033[92m'
    WARNING = '\033[93m'
    FAIL = '\033[91m'
    ENDC = '\033[0m'
    BOLD = '\033[1m'
    UNDERLINE = '\033[4m'

In [60]:
%%cython
import numpy as np
cimport numpy as np
cimport cython

import sys
import time


DTYPE_INT32 = np.int32
ctypedef np.int32_t DTYPE_INT32_t

DTYPE_FLOAT = np.float64
ctypedef np.float64_t DTYPE_FLOAT_t

cdef DTYPE_FLOAT_t MAX_FLOAT = float('inf')

# careful, without bounds checking can mess up memory - also can't use negative indices I think (like x[-1])
@cython.boundscheck(False) # turn off bounds-checking for entire function
def Segment_DP(np.ndarray[DTYPE_FLOAT_t, ndim=2] C, np.ndarray[np.int32_t, ndim=2] T):

    cdef DTYPE_INT32_t numRows = C.shape[0]
    cdef DTYPE_INT32_t numCols = C.shape[1]    
    cdef np.ndarray[np.int32_t, ndim=2] steps = np.zeros((numRows+1,numCols), dtype=np.int32)
    cdef np.ndarray[DTYPE_FLOAT_t, ndim=2] accumCost = np.ones((numRows+1, numCols), dtype=DTYPE_FLOAT) * MAX_FLOAT

    cdef unsigned int row, col
    cdef DTYPE_FLOAT_t skipCost
    cdef np.int32_t jumpStartCol
    cdef DTYPE_FLOAT_t jumpCost

    # initialize
    for row in range(numRows+1):
        for col in range(numCols):
            steps[row, col] = -1 # skip by default
    for col in range(numCols):
        accumCost[0, col] = 0 # all inf except first row
        
    # dynamic programming
    for row in range(1, numRows+1):
        for col in range(numCols):
            
            # skip transition
            if col == 0:
                skipCost = MAX_FLOAT
            else:
                skipCost = accumCost[row, col-1]
            accumCost[row, col] = skipCost
            # best step is skip by default, so don't need to assign
            
            # jump transition
            jumpStartCol = T[row-1, col]
            if jumpStartCol >= 0: # valid subsequence path
                jumpCost = accumCost[row-1, jumpStartCol] + C[row-1, col]
                if jumpCost < skipCost:
                    accumCost[row, col] = jumpCost
                    steps[row, col] = jumpStartCol

    return [accumCost, steps]

@cython.boundscheck(False) # turn off bounds-checking for entire function
def Segment_Backtrace(np.ndarray[DTYPE_FLOAT_t, ndim=2] accumCost, np.ndarray[np.int32_t, ndim=2] steps):

    cdef np.uint32_t numRows = accumCost.shape[0]
    cdef np.uint32_t numCols = accumCost.shape[1]
    cdef np.uint32_t curRow = numRows - 1
    cdef np.uint32_t curCol = numCols - 1
    cdef np.int32_t jump
    cdef np.ndarray[np.uint32_t, ndim=1] path = np.zeros(numRows-1, dtype=np.uint32)
    cdef np.uint32_t pathElems = 0

    while curRow > 0:
        if accumCost[curRow, curCol] == MAX_FLOAT:
            print('A path is not possible')
            break

        jump = steps[curRow, curCol]
        if jump < 0: # skip
            curCol = curCol - 1
        else: # jump
            path[pathElems] = curCol
            pathElems = pathElems + 1
            curRow = curRow - 1
            curCol = jump

    return path[::-1]

@cython.boundscheck(False) # turn off bounds-checking for entire function
def calc_Tseg(np.ndarray[DTYPE_FLOAT_t, ndim=2] accumCost, np.ndarray[np.uint32_t, ndim=2] stepsForCost, parameter):
    '''

    Parameter should have: 'dn', 'dm'
    '''

    cdef np.ndarray[unsigned int, ndim=1] dn
    cdef np.ndarray[unsigned int, ndim=1] dm
    cdef np.uint32_t numRows = accumCost.shape[0]
    cdef np.uint32_t numCols = accumCost.shape[1]
    cdef np.ndarray[np.int32_t, ndim=1] startLocs = np.zeros(numCols, dtype=np.int32)
    cdef np.uint32_t endCol
    cdef np.uint32_t curRow
    cdef np.uint32_t curCol
    cdef np.uint32_t curStepIndex

    # get step transitions
    if ('dn'  in parameter.keys()):
        dn = parameter['dn']
    else:
        dn = np.array([1, 1, 0], dtype=DTYPE_INT32)
    if 'dm'  in parameter.keys():
        dm = parameter['dm']
    else:
        dm = np.array([1, 0, 1], dtype=DTYPE_INT32)

    # backtrace from every location
    for endCol in range(numCols):
        curCol = endCol
        curRow = numRows - 1
        while curRow > 0:
            if accumCost[curRow, curCol] == MAX_FLOAT: # no valid path
                startLocs[curCol] = -1
                break

            curStepIndex = stepsForCost[curRow, curCol]
            curRow = curRow - dn[curStepIndex]
            curCol = curCol - dm[curStepIndex]
            if curRow == 0:
                startLocs[endCol] = curCol
                
    return startLocs

class bcolors:
    HEADER = '\033[95m'
    OKBLUE = '\033[94m'
    OKGREEN = '\033[92m'
    WARNING = '\033[93m'
    FAIL = '\033[91m'
    ENDC = '\033[0m'
    BOLD = '\033[1m'
    UNDERLINE = '\033[4m'

In [61]:
def alignSSDTW(featfile1, featfile2, steps, weights, downsample, numSegments, outfile = None, profile = False):
    
    # compute cost matrix
    F1 = np.load(featfile1) # 12 x N
    F2 = np.load(featfile2) # 12 x M
    swap = (F1.shape[1] > F2.shape[1])
    if swap:
        F1, F2 = F2, F1 # make the shorter sequence the query
    if max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2: # no valid path possible
        if outfile:
            pickle.dump(None, open(outfile, 'wb'))
        return None
    times = []
    times.append(time.time())
    C = 1 - F1[:,0::downsample].T @ F2[:,0::downsample] # cos distance metric
    times.append(time.time())
    
    # run subseqDTW on chunks
    seglen = int(np.ceil(F1.shape[1] / numSegments))
    dn = steps[:,0].astype(np.uint32)
    dm = steps[:,1].astype(np.uint32)
    dw = weights
    params1 = {'dn': dn, 'dm': dm, 'dw': dw, 'SubSequence': True}
    Dparts = []
    Bparts = []
    for i in range(numSegments):
        Cpart = C[i*seglen : min((i+1)*seglen, F1.shape[1]), :]
        [D, B] = DTW_Cost_To_AccumCostAndSteps(Cpart, params1)
        Dparts.append(D)
        Bparts.append(B)
    times.append(time.time())
    
    # construct Cseg, Tseg
    Cseg = np.zeros((numSegments, F2.shape[1]))
    Tseg = np.zeros((numSegments, F2.shape[1]), dtype=np.int32)
    for i, Dpart in enumerate(Dparts):
        Cseg[i,:] = Dpart[-1,:]
        Tseg[i,:] = calc_Tseg(Dpart, Bparts[i], params1)
    times.append(time.time())
    
    # segment-level DP
    [Dseg, Bseg] = Segment_DP(Cseg, Tseg)
    times.append(time.time())
    segmentEndIdxs = Segment_Backtrace(Dseg, Bseg)
    times.append(time.time())
    
    # backtrace on chunks
    wps = []
    for i, endidx in enumerate(segmentEndIdxs):
        params2 = {'dn': dn, 'dm': dm, 'dw': dw, 'SubSequence': True, 'startCol': endidx}
        [wpchunk, _, _] = DTW_GetPath(Dparts[i], Bparts[i], params2)
        wpchunk[0,:] = wpchunk[0,:] + i*seglen  # account for relative offset
        wps.append(wpchunk.copy())
    wp_merged = np.hstack(wps)
    times.append(time.time())
    
    if swap:
        wp_merged = np.flipud(wp_merged) # undo swap
    
    if outfile:
        pickle.dump(wp_merged, open(outfile, 'wb'))
    
    if profile:
        return wp_merged, np.diff(times)
    else:
        return wp_merged

In [62]:
def alignSegmentalDTW_batch(querylist, featdir1, featdir2, outdir, n_cores, steps, weights, downsample, numSegments, fn):

    outdir.mkdir(parents=True, exist_ok=True)
    
    # prep inputs for parallelization
    inputs = []
    with open(querylist, 'r') as f:
        for line in f:
            parts = line.strip().split(' ')
            assert len(parts) == 2
            featfile1 = (featdir1 / parts[0]).with_suffix('.npy')
            featfile2 = (featdir2 / parts[1]).with_suffix('.npy')
            queryid = os.path.basename(parts[0]) + '__' + os.path.basename(parts[1])
            outfile = (outdir / queryid).with_suffix('.pkl')
            if os.path.exists(outfile):
                print(f"Skipping {outfile}")
            else:
                inputs.append((featfile1, featfile2, steps, weights, downsample, numSegments, outfile))

    # process files in parallel
    pool = multiprocessing.Pool(processes = n_cores)
    pool.starmap(fn, inputs)

    return

In [71]:
# query_list = 'cfg_files/query.train.list'
# featdir1 = Path('features/clean')
# featdir2 = Path('features/clean') # in case you want to align clean vs noisy
# n_cores = 10
# steps = subseqDTWDefaultSteps.T#np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights#np.array([1,1,2])
# downsample = 1
# segmentVals = [2, 4, 8, 16, 32]
# for numSegments in segmentVals:
#     outdir = Path(f'experiments_train/ssdtw_cython_{numSegments}_clean')
#     try:
#         os.mkdir(outdir)
#     except:
#         print(outdir, " already exists")
    
#     alignSegmentalDTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, downsample, numSegments, alignSSDTW)

experiments_train/ssdtw_cython_2_clean  already exists
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Ashkenazy-1981_pid9058-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Beliavsky-2004_pid9152-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Ben-Or-1989_pid9161-12.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Biret-1990_pid9062-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Blet-2003_pid9103-07.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Block-1995_pid9064-04.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Brailowsky-1960_pid9060-1

Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-1990_pid9062-13__Chopin_Op017No4_Osinska-1989_pid9101-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-1990_pid9062-13__Chopin_Op017No4_Paderewski-1912_pid5667274-09.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-1990_pid9062-13__Chopin_Op017No4_Perahia-1994_pid54293-09.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-1990_pid9062-13__Chopin_Op017No4_Perlemuter-1986_pid9089-15.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-1990_pid9062-13__Chopin_Op017No4_Poblocka-1999_pid9093-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-1990_pid9062-13__Chopin_Op017No4_Rangell-2001_pid9094-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-1990_pid9062-13__Chopin_Op017No4_Risler-1920_pid9132-11.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Biret-199

Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fliere-1977_pid9063-13__Chopin_Op017No4_Milkina-1970_pid9099-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fliere-1977_pid9063-13__Chopin_Op017No4_Mohovich-1999_pid9104-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fliere-1977_pid9063-13__Chopin_Op017No4_Nadelmann-1956_pid9165-04.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fliere-1977_pid9063-13__Chopin_Op017No4_Ohlsson-1999_pid9153-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fliere-1977_pid9063-13__Chopin_Op017No4_Olejniczac-1990_pid9100b-17.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fliere-1977_pid9063-13__Chopin_Op017No4_Olejniczak-1991_pid9087-07.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fliere-1977_pid9063-13__Chopin_Op017No4_Osinska-1989_pid9101-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Fl

Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kitain-1937_pid9163-02__Chopin_Op017No4_Magaloff-1977_pid5667267b-10.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kitain-1937_pid9163-02__Chopin_Op017No4_Magaloff-1977_pid9074f-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kitain-1937_pid9163-02__Chopin_Op017No4_Magin-1975_pid9138-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kitain-1937_pid9163-02__Chopin_Op017No4_Milkina-1970_pid9099-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kitain-1937_pid9163-02__Chopin_Op017No4_Mohovich-1999_pid9104-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kitain-1937_pid9163-02__Chopin_Op017No4_Nadelmann-1956_pid9165-04.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kitain-1937_pid9163-02__Chopin_Op017No4_Ohlsson-1999_pid9153-13.pkl
Skipping experiments_train/ssdtw_cython_2_clean/Chopin_Op017No4_Kita

experiments_train/ssdtw_cython_4_clean  already exists
Skipping experiments_train/ssdtw_cython_4_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Ashkenazy-1981_pid9058-13.pkl
Skipping experiments_train/ssdtw_cython_4_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Beliavsky-2004_pid9152-13.pkl
Skipping experiments_train/ssdtw_cython_4_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Ben-Or-1989_pid9161-12.pkl
Skipping experiments_train/ssdtw_cython_4_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Biret-1990_pid9062-13.pkl
Skipping experiments_train/ssdtw_cython_4_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Blet-2003_pid9103-07.pkl
Skipping experiments_train/ssdtw_cython_4_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Block-1995_pid9064-04.pkl
Skipping experiments_train/ssdtw_cython_4_clean/Chopin_Op017No4_Afanassiev-2001_pid9130-01__Chopin_Op017No4_Brailowsky-1960_pid9060-1

...

Process ForkPoolWorker-146:
Process ForkPoolWorker-112:
Process ForkPoolWorker-149:
Process ForkPoolWorker-133:
Process ForkPoolWorker-104:
Process ForkPoolWorker-137:
Process ForkPoolWorker-123:
Process ForkPoolWorker-110:
Process ForkPoolWorker-144:
Process ForkPoolWorker-150:
Process ForkPoolWorker-135:
Process ForkPoolWorker-139:
Process ForkPoolWorker-103:
Process ForkPoolWorker-128:
Process ForkPoolWorker-145:
Process ForkPoolWorker-122:
Process ForkPoolWorker-121:
Process ForkPoolWorker-106:
Process ForkPoolWorker-108:
Process ForkPoolWorker-130:
Process ForkPoolWorker-107:
Process ForkPoolWorker-113:
Process ForkPoolWorker-119:
Process ForkPoolWorker-116:
Process ForkPoolWorker-101:
Process ForkPoolWorker-114:
Process ForkPoolWorker-102:
Process ForkPoolWorker-138:
Process ForkPoolWorker-129:
Process ForkPoolWorker-109:
Process ForkPoolWorker-134:
Process ForkPoolWorker-131:
Process ForkPoolWorker-120:
Process ForkPoolWorker-105:
Process ForkPoolWorker-125:
Process ForkPoolWork

  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
Traceback (most recent call last):
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
   

  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/connection.py", line 216, in recv_bytes
    buf = self._recv_bytes(maxlength)
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/po

KeyboardInterrupt
KeyboardInterrupt
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/connection.py", line 216, in recv_bytes
    buf = self._recv_bytes(maxlength)
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/connection.py", line 407, in _recv_bytes
    buf = self._recv(4)
KeyboardInterrupt
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/

  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/tshaw/anaconda3/envs/segDTW/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  F

## Aligning Noisy

In [64]:
def runSimulation(featdir1, featdir2, query_list, outdir):
    DTWDefaultSteps = np.array([[1, 1, 2],
                            [1, 2, 1]], dtype = np.uint32)

    DTWDefaultWeights = np.array([2, 3, 3], dtype = np.float64)


    subseqDTWDefaultSteps = np.array([[1, 1, 2],
                                      [1, 2, 1]], dtype = np.uint32)

    subseqDTWDefaultWeights = np.array([1, 1, 2], dtype = np.float64)

    try:
        os.mkdir(outdir)
        os.mkdir(outdir / "DTW")
        for K in [2, 4, 8, 16, 32]:
            subdir = outdir / ("WSDTW_%s" % str(K))
            os.mkdir(subdir)
    except:
        print("Failed to make directories")
    
    # Prepping inputs
    DTWInputs = []
    WSDTWInputs = {2: [], 4: [], 8: [], 16: [], 32: [],}
    with open(query_list, 'r') as f:
        for line in f:
            parts = line.strip().split(' ')
            assert len(parts) == 2
            featfile1 = (featdir1 / parts[0]).with_suffix('.npy')
            featfile2 = (featdir2 / parts[1]).with_suffix('.npy')
            
            queryid = os.path.basename(parts[0]) + '__' + os.path.basename(parts[1])
            DTWoutfile = (outdir / "DTW" / queryid).with_suffix('.pkl')
            
            if os.path.exists(DTWoutfile):
                print(f"Skipping {DTWoutfile}")
            else:
                DTWInputs.append((featfile1, featfile2, DTWDefaultSteps, DTWDefaultWeights, False, DTWoutfile, False))
            
            for K in WSDTWInputs.keys():
                outfile = (outdir / ("WSDTW_%s" % str(K)) / queryid).with_suffix('.pkl')
                if os.path.exists(outfile):
                    print(f"Skipping {outfile}")
                else:
                    WSDTWInputs[K].append((featfile1, featfile2, K, subseqDTWDefaultSteps, subseqDTWDefaultWeights,\
                                       outfile, False))
    
    # Run DTW
    print("Running DTW")
    pool = multiprocessing.Pool(processes = 10)
    pool.starmap(DTW, DTWInputs)
    
    #Run WSDTW with different numbers of segments
    print("Running WSDTW")
    for K in WSDTWInputs.keys():
        print("K =", K)
        pool.starmap(WSDTW, WSDTWInputs[K])

In [65]:
# query_list = 'cfg_files/query.train.list'
# featdir1 = Path('features/clean')
# featdir2 = Path('features/noisy_20dB')

# outdir = Path('experiments_train/noisy_20dB')

# runSimulation(featdir1, featdir2, query_list, outdir)

In [66]:
# for SNR in [-10, -5, 0, 5, 10, 15, 20]:
#     query_list = 'cfg_files/query.train.list'
#     featdir1 = Path('features/clean')
#     featdir2 = Path(('features/noisy_%sdB' % str(SNR)))

#     outdir = Path(('experiments_train/noisy_%sdB' % str(SNR)))

#     runSimulation(featdir1, featdir2, query_list, outdir)

# Run Alignments on Test Data

In [ ]:
# DTW
query_list = 'cfg_files/query.test.list'
featdir1 = Path('features/clean')
featdir2 = Path('features/clean') # in case you want to align clean vs noisy
outdir = Path('experiments_test/clean/dtw')
try:
    os.mkdir(outdir)
except:
    print(outdir, " already exists")
n_cores = 10
steps = DTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
weights = DTWDefaultWeights #np.array([2,3,3])
downsample = 1
inputs = DTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, False)

# NSDTW
query_list = 'cfg_files/query.test.list'
featdir1 = Path('features/clean')
featdir2 = Path('features/clean') # in case you want to align clean vs noisy
n_cores = 10
steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
weights = subseqDTWDefaultWeights #np.array([1,1,2])
downsample = 1
segmentVals = [2, 4, 8, 16, 32] 
for numSegments in segmentVals:
    outdir = Path(f'experiments_test/clean/nsdtw_{numSegments}')
    try:
        os.mkdir(outdir)
    except:
        print(outdir, " already exists")
    SDTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, numSegments, NSDTW)

# WSDTW
query_list = 'cfg_files/query.test.list'
featdir1 = Path('features/clean')
featdir2 = Path('features/clean') # in case you want to align clean vs noisy
n_cores = 10
steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
weights = subseqDTWDefaultWeights #np.array([1,1,2])
downsample = 1
segmentVals = [2, 4, 8, 16, 32] 
for numSegments in segmentVals:
    outdir = Path(f'experiments_test/clean/wsdtw_{numSegments}')
    try:
        os.mkdir(outdir)
    except:
        print(outdir, " already exists")
    SDTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, numSegments, WSDTW)

# SSDTW
query_list = 'cfg_files/query.test.list'
featdir1 = Path('features/clean')
featdir2 = Path('features/clean') # in case you want to align clean vs noisy
n_cores = 10
steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
weights = subseqDTWDefaultWeights #np.array([1,1,2])
downsample = 1
segmentVals = [2, 4, 8, 16, 32] 
for numSegments in segmentVals:
    print(numSegments)
    outdir = Path(f'experiments_test/clean/ssdtw_{numSegments}')
    try:
        os.mkdir(outdir)
    except:
        print(outdir, " already exists")
    SDTW_batch(query_list, featdir1, featdir2, outdir, n_cores, steps, weights, numSegments, SSDTW)

# Noisy
for SNR in [-10, -5, 0, 5, 10, 15, 20]:
    query_list = 'cfg_files/query.test.list'
    featdir1 = Path('features/clean')
    featdir2 = Path(('features/noisy_%sdB' % str(SNR)))

    outdir = Path(('experiments_test/noisy_%sdB' % str(SNR)))

    runSimulation(featdir1, featdir2, query_list, outdir)

experiments_test/clean/dtw  already exists
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Ax-1985_pid9179-07.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Bacha-1998_pid9166e-08.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Barbosa-1983_pid9174-15.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Ben-Or-1989_pid9161-13.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Biret-1990_pid9062-15.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Brailowsky-1960_pid9060-15.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Chiu-1999_pid9048-15.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Ashkenazy-1981_pid9058-15__Chopin_Op024No2_Clidat-199

Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Hatto-2006_pid9073-17.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Horszowski-1983_pid9131-12.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Indjic-1988_pid9050-15.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Katin-1996_pid9126-03.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Kiepura-1999_pid9098-02.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Korecka-Soszkowska-1992_pid9128-11.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Kushner-1990_pid9118-15.pkl
Skipping experiments_test/clean/dtw/Chopin_Op024No2_Francois-1956_pid9070-23__Chopin_Op024No2_Lilamand-2001_pid9186c-15.pkl
Skipping expe

Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Poblocka-1999_pid9093-19.pkl
Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Rangell-2001_pid9094-19.pkl
Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Rubinstein-1939_pid9049-19.pkl
Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Rubinstein-1952_pid9075-19.pkl
Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Rubinstein-1966_pid9059-19.pkl
Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Shebanova-2002_pid9072-19.pkl
Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Smith-1975_pid9054-19.pkl
Skipping experiments_test/clean/dtw/Chopin_Op030No2_Cortot-1951_pid9066-19__Chopin_Op030No2_Sofronitsky-1960_pid5667291-15.pkl
Skipping experiments_te

Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Duchoud-2007_pid610633-01.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Ezaki-2006_pid9139b-12.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Falvay-1989_pid9068-20.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Farrell-1958_pid918805-02.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Ferenczy-1958_pid9097-24.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Fliere-1977_pid9063b-16.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Fou-1978_pid9071b-22.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Blumental-1952_pid9102-07__Chopin_Op063No3_Francois-1956_pid9070b-24.pkl
Skipping exper

Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Rubinstein-1952_pid9075b-12.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Rubinstein-1966_pid9059b-16.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Schilhawsky-1960_pid9129-17.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Shebanova-2002_pid9072b-16.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Smith-1975_pid9054b-12.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Sokolov-2002_pid610633-06.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Sztompka-1959_pid9170b-12.pkl
Skipping experiments_test/clean/dtw/Chopin_Op063No3_Ferenczy-1958_pid9097-24__Chopin_Op063No3_Tomsic-1995_pid9190-09.pkl
Skippin

...

Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__Chopin_Op063No3_Rubinstein-1939_pid9049b-12.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__Chopin_Op063No3_Rubinstein-1952_pid9075b-12.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__Chopin_Op063No3_Rubinstein-1966_pid9059b-16.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__Chopin_Op063No3_Schilhawsky-1960_pid9129-17.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__Chopin_Op063No3_Shebanova-2002_pid9072b-16.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__Chopin_Op063No3_Smith-1975_pid9054b-12.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__Chopin_Op063No3_Sokolov-2002_pid610633-06.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Garcia-Casas_pid610633-07__

Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kissin-1993_pid9056-07__Chopin_Op063No3_Sztompka-1959_pid9170b-12.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kissin-1993_pid9056-07__Chopin_Op063No3_Tomsic-1995_pid9190-09.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kissin-1993_pid9056-07__Chopin_Op063No3_Uninsky-1932_pid9085-11.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kissin-1993_pid9056-07__Chopin_Op063No3_Uninsky-1971_pid9061b-09.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kissin-1993_pid9056-07__Chopin_Op063No3_Wasowski-1980_pid9111b-14.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kissin-1993_pid9056-07__Chopin_Op063No3_Zak-1937_pid9085-12.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kissin-1993_pid9056-07__Chopin_Op063No3_Zak-1951_pid918713-20.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Kushner-1989_pid9118b-16__Chopin_Op063No3_Luisada-1991_pid9055b-12.pkl

Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Tomsic-1995_pid9190-09__Chopin_Op063No3_Zak-1951_pid918713-20.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Uninsky-1932_pid9085-11__Chopin_Op063No3_Uninsky-1971_pid9061b-09.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Uninsky-1932_pid9085-11__Chopin_Op063No3_Wasowski-1980_pid9111b-14.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Uninsky-1932_pid9085-11__Chopin_Op063No3_Zak-1937_pid9085-12.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Uninsky-1932_pid9085-11__Chopin_Op063No3_Zak-1951_pid918713-20.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Uninsky-1971_pid9061b-09__Chopin_Op063No3_Wasowski-1980_pid9111b-14.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Uninsky-1971_pid9061b-09__Chopin_Op063No3_Zak-1937_pid9085-12.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op063No3_Uninsky-1971_pid9061b-09__Chopin_Op063No3_Zak-1951_pid918713-20.pkl

Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Jonas-1947_pid9096-03.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Kapell-1951_pid9090-26.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Kiepura-1999_pid9098-07.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Kushner-1989_pid9118b-25.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Luisada-1991_pid9055b-19.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Lushtak-2004_pid9088-25.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Magaloff-1978_pid9074g-19.pkl
Skipping experiments_test/clean/nsdtw_32/Chopin_Op068No3_Indjic-1988_pid9050b-21__Chopin_Op068No3_Meguri-1997_pid9137

experiments_test/clean/wsdtw_2  already exists


### Runtime Profiling

In [63]:
def saveRandomFeatureMatrices(sizes, outdir):
    
    if not os.path.exists(outdir):
        os.mkdir(outdir)
    
    np.random.seed(0)
    for sz in sizes:
        F = np.random.rand(12, sz)
        outfile = outdir + f'/F_{sz}.npy'
        np.save(outfile, F)
    
    return

In [64]:
# sizes = [1000, 2000, 5000, 10000, 20000, 50000]
rand_feat_dir = 'features/random'
# saveRandomFeatureMatrices(sizes, rand_feat_dir)

Profile All

In [ ]:
# # DTW
# print("DTW")
# outfile = 'dtw_prof.pkl'
# steps = DTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = DTWDefaultWeights #np.array([2,3,3])
# subsequence = False
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(sizes), N, 3)) # DTW runtime is broken into 3 parts
# for i in range(len(sizes)):
#     sz = sizes[i]
#     print(f'Running size = {sz} ', end='')
#     featfile = rand_feat_dir + f'/F_{sz}.npy'
#     for j in range(N):
#         print('.', end='')
#         gc.collect()
#         _, times = DTW(featfile, featfile, steps, weights, subsequence, profile=True)
#         durs[i,j,:] = np.array(times)
#     print('')
# pickle.dump([durs, sizes], open(outfile, 'wb'))

# # Subsequence DTW
# print("Subsequence DTW")
# outfile = 'subsequence_dtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([2,3,3])
# subsequence = True
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(sizes), N, 3)) # DTW runtime is broken into 3 parts
# for i in range(len(sizes)):
#     sz = sizes[i]
#     print(f'Running size = {sz} ', end='')
#     featfile = rand_feat_dir + f'/F_{sz}.npy'
#     for j in range(N):
#         print('.', end='')
#         gc.collect()
#         _, times = DTW(featfile, featfile, steps, weights, subsequence, profile=True)
#         durs[i,j,:] = np.array(times)
#     print('')
# pickle.dump([durs, sizes], open(outfile, 'wb'))

# # NSDTW
# print("NSDTW")
# outfile = 'nsdtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# segmentVals = [2, 4, 8, 16, 32]
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(segmentVals), len(sizes), N, 3)) # NSDTW runtime is broken into 3 parts
# for i, numSegments in enumerate(segmentVals):
#     print(f'Running numSegments = {numSegments} ', end='')
#     for j, sz in enumerate(sizes):
#         print('|', end='')
#         featfile = rand_feat_dir + f'/F_{sz}.npy'
#         for k in range(N):
#             print('.', end='')
#             gc.collect()
#             _, times = NSDTW(featfile, featfile, numSegments, steps, weights, profile=True)
#             durs[i,j,k,:] = np.array(times)
#     print('')
# pickle.dump([durs, segmentVals, sizes], open(outfile, 'wb'))

# # WSDTW
# print("WSDTW")
# outfile = 'wsdtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# segmentVals = [2, 4, 8, 16, 32]
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(segmentVals), len(sizes), N, 5)) # WSDTW runtime is broken into 5 parts
# for i, numSegments in enumerate(segmentVals):
#     print(f'Running numSegments = {numSegments} ', end='')
#     for j, sz in enumerate(sizes):
#         print('|', end='')
#         featfile = rand_feat_dir + f'/F_{sz}.npy'
#         for k in range(N):
#             print('.', end='')
#             gc.collect()
#             _, times = WSDTW(featfile, featfile, numSegments, steps, weights, profile=True)
#             durs[i,j,k,:] = np.array(times)
#     print('')
# pickle.dump([durs, segmentVals, sizes], open(outfile, 'wb'))


# # SSDTW
# print("SSDTW")
# outfile = 'ssdtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# segmentVals = [2, 4, 8, 16, 32]
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(segmentVals), len(sizes), N, 5)) # SSDTW runtime is broken into 5 parts
# for i, numSegments in enumerate(segmentVals):
#     print(f'Running numSegments = {numSegments} ', end='')
#     for j, sz in enumerate(sizes):
#         print('|', end='')
#         featfile = rand_feat_dir + f'/F_{sz}.npy'
#         for k in range(N):
#             print('.', end='')
#             gc.collect()
#             _, times = SSDTW(featfile, featfile, numSegments, steps, weights, profile=True)
#             durs[i,j,k,:] = np.array(times)
#     print('')
# pickle.dump([durs, segmentVals, sizes], open(outfile, 'wb'))

DTW
Running size = 50000 .

Profiling DTW

In [ ]:
# DTW
# outfile = 'dtw_prof.pkl'
# steps = DTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = DTWDefaultWeights #np.array([2,3,3])
# subsequence = False
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(sizes), N, 3)) # DTW runtime is broken into 3 parts
# for i in range(len(sizes)):
#     sz = sizes[i]
#     print(f'Running size = {sz} ', end='')
#     featfile = rand_feat_dir + f'/F_{sz}.npy'
#     for j in range(N):
#         print('.', end='')
#         gc.collect()
#         _, times = DTW(featfile, featfile, steps, weights, subsequence, profile=True)
#         durs[i,j,:] = np.array(times)
#     print('')
# pickle.dump([durs, sizes], open(outfile, 'wb'))

Profiling Subsequence DTW

In [ ]:
# Subsequence DTW
# outfile = 'subsequence_dtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([2,3,3])
# subsequence = True
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(sizes), N, 3)) # DTW runtime is broken into 3 parts
# for i in range(len(sizes)):
#     sz = sizes[i]
#     print(f'Running size = {sz} ', end='')
#     featfile = rand_feat_dir + f'/F_{sz}.npy'
#     for j in range(N):
#         print('.', end='')
#         gc.collect()
#         _, times = DTW(featfile, featfile, steps, weights, subsequence, profile=True)
#         durs[i,j,:] = np.array(times)
#     print('')
# pickle.dump([durs, sizes], open(outfile, 'wb'))

Profiling NSDTW

In [ ]:
# NSDTW
# outfile = 'nsdtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# segmentVals = [2, 4, 8, 16, 32]
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(segmentVals), len(sizes), N, 3)) # NSDTW runtime is broken into 3 parts
# for i, numSegments in enumerate(segmentVals):
#     print(f'Running numSegments = {numSegments} ', end='')
#     for j, sz in enumerate(sizes):
#         print('|', end='')
#         featfile = rand_feat_dir + f'/F_{sz}.npy'
#         for k in range(N):
#             print('.', end='')
#             gc.collect()
#             _, times = NSDTW(featfile, featfile, numSegments, steps, weights, profile=True)
#             durs[i,j,k,:] = np.array(times)
#     print('')
# pickle.dump([durs, segmentVals, sizes], open(outfile, 'wb'))

Profiling WSDTW

In [ ]:
# WSDTW
# outfile = 'wsdtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# segmentVals = [2, 4, 8, 16, 32]
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(segmentVals), len(sizes), N, 5)) # WSDTW runtime is broken into 5 parts
# for i, numSegments in enumerate(segmentVals):
#     print(f'Running numSegments = {numSegments} ', end='')
#     for j, sz in enumerate(sizes):
#         print('|', end='')
#         featfile = rand_feat_dir + f'/F_{sz}.npy'
#         for k in range(N):
#             print('.', end='')
#             gc.collect()
#             _, times = WSDTW(featfile, featfile, numSegments, steps, weights, profile=True)
#             durs[i,j,k,:] = np.array(times)
#     print('')
# pickle.dump([durs, segmentVals, sizes], open(outfile, 'wb'))

Profiling SSDTW

In [ ]:
# SSDTW
# outfile = 'ssdtw_prof.pkl'
# steps = subseqDTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
# weights = subseqDTWDefaultWeights #np.array([1,1,2])
# segmentVals = [2, 4, 8, 16, 32]
# sizes = [50000, 20000, 10000, 5000, 2000, 1000]
# N = 10
# durs = np.zeros((len(segmentVals), len(sizes), N, 5)) # SSDTW runtime is broken into 5 parts
# for i, numSegments in enumerate(segmentVals):
#     print(f'Running numSegments = {numSegments} ', end='')
#     for j, sz in enumerate(sizes):
#         print('|', end='')
#         featfile = rand_feat_dir + f'/F_{sz}.npy'
#         for k in range(N):
#             print('.', end='')
#             gc.collect()
#             _, times = SSDTW(featfile, featfile, numSegments, steps, weights, profile=True)
#             durs[i,j,k,:] = np.array(times)
#     print('')
# pickle.dump([durs, segmentVals, sizes], open(outfile, 'wb'))

DTW With Cython Backtrace

In [65]:
# Compile this function in object mode to allow for np.load and time profiling
@jit(forceobj = True)
def DTW_V2(queryFeatureFile, refFeatureFile, Steps = DTWDefaultSteps, weights = DTWDefaultWeights, subsequence = False, \
        outfile = None, profile = False):
    '''
    Run DTW on query and reference feature matrices
    
    Arguments:
    queryFeatureFile -- The file containing the query feature matrix
    refFeatureFile -- The file containing the reference feature matrix
    Steps -- The steps matrix. The first row is the steps in along the rows,
             the second row is the steps along the columns
    weights -- The weights for the steps
    subsequence -- True if subsequence DTW should be performed rather than standard DTW
    
    Returns:
    path -- A 2d numpy array storing the optimal path. The first row is the path through the rows.
            The second row is the path through the columns
    '''
    # Extract Feature matrices
    F1 = np.load(queryFeatureFile, allow_pickle = True)
    F2 = np.load(refFeatureFile, allow_pickle = True)
    
    # empty file if no valid path possible
    if not subsequence and max(F1.shape[1], F2.shape[1]) / min(F1.shape[1], F2.shape[1]) >= 2:
        if outfile:
            pickle.dump(None, open(outfile, 'wb'))
        return None
    
    # start time logging
    times = []
    times.append(time.time())
    
    # Compute Cost Matrix
    C = 1 - F1.T @ F2 # cos distance metric
    
    times.append(time.time())
    
    # Get D and B
    D, B = DTW_Cost_To_DandB(C, Steps = Steps, weights = weights, subsequence=subsequence)
    
    times.append(time.time())
    
    # Backtrace and return
    rowSteps = Steps[0,:]
    colSteps = Steps[1,:]
    params = {"dn": rowSteps, "dm": colSteps, "dw": weights, "SubSequence": True}
    wp = DTW_GetPath(D, B, params)
    
    times.append(time.time())
    
    # logging result if outfile exists
    if outfile:
        pickle.dump(wp, open(outfile, 'wb'))
    
    # return extra timing array if profiling timing
    if profile:
        return wp, np.diff(times)
    else:
        return wp

In [ ]:
# DTW V2
outfile = 'profiles/dtw_V2_prof.pkl'
steps = DTWDefaultSteps #np.array([1,1,1,2,2,1]).reshape((-1,2))
weights = DTWDefaultWeights #np.array([2,3,3])
subsequence = False
sizes = [50000, 20000, 10000, 5000, 2000, 1000]
N = 10
durs = np.zeros((len(sizes), N, 3)) # DTW runtime is broken into 3 parts
for i in range(len(sizes)):
    sz = sizes[i]
    print(f'Running size = {sz} ', end='')
    featfile = rand_feat_dir + f'/F_{sz}.npy'
    for j in range(N):
        print('.', end='')
        gc.collect()
        _, times = DTW_V2(featfile, featfile, steps, weights, subsequence, profile=True)
        durs[i,j,:] = np.array(times)
    print('')
pickle.dump([durs, sizes], open(outfile, 'wb'))

Running size = 50000 .